In [1]:
import time
import pywikibot
import mwparserfromhell
import csv
import json
import re
import xml.sax
from bs4 import BeautifulSoup
import requests


In [2]:
site = pywikibot.Site("id", "wikipedia")
art = pywikibot.Page(site, 'Raden Mattaher')


wikicode = mwparserfromhell.parse(art.get())
matches = wikicode.filter_templates(matches = "Infobox")
properties = {param.name.strip(): param.value
                                for param in matches[0].params}
print(properties)

{'name': ' Raden Mattaher\n', 'image': ' Raden Mattaher.jpg\n', 'imagesize': ' 200px\n', 'alt': ' \n', 'caption': ' \n', 'birth_name': ' \n', 'birth_date': ' 1871\n', 'birth_place': ' Dusun Sekamis, [[Kesultanan Jambi]]\n', 'death_date': ' {{death date and age|1907|9|10|1871|df=y}}\n', 'death_place': ' Dusun Muaro Jambi, [[Keresidenan Jambi]], [[Hindia Belanda]]\n', 'other_names': ' Raden Mohammad Tahir, Pangeran Mattahir\n', 'known_for': " Pejuang Kemerdekaan [[Indonesia]] dari [[Jambi]], dan [[Pahlawan Nasional Indonesia]]<ref>[https://m.republika.co.id/amp/qjk8kb335 Raden Mattaher, Singo Kumpeh yang Jadi Pahlawan Nasional] ''republika'' 10 November 2020</ref>\n", 'occupation': ' \n', 'religion': ' \n', 'spouse': ' \n', 'children': ' \n', 'parents': ' Raden Kusin (ayah)<br> Ratumas Esa (ibu)\n', 'relatives': ' [[Sultan Thaha Syaifuddin]] (kakek)\n'}


In [62]:
print(matches)

["{{Infobox person\n| name               = Raden Mattaher\n| image              = Raden Mattaher.jpg\n| imagesize          = 200px\n| alt                = \n| caption            = \n| birth_name         = \n| birth_date         = 1871\n| birth_place        = Dusun Sekamis, [[Kesultanan Jambi]]\n| death_date         = {{death date and age|1907|9|10|1871|df=y}}\n| death_place        = Dusun Muaro Jambi, [[Keresidenan Jambi]], [[Hindia Belanda]]\n| other_names        = Raden Mohammad Tahir, Pangeran Mattahir\n| known_for          = Pejuang Kemerdekaan [[Indonesia]] dari [[Jambi]], dan [[Pahlawan Nasional Indonesia]]<ref>[https://m.republika.co.id/amp/qjk8kb335 Raden Mattaher, Singo Kumpeh yang Jadi Pahlawan Nasional] ''republika'' 10 November 2020</ref>\n| occupation         = \n| religion           = \n| spouse             = \n| children           = \n| parents            = Raden Kusin (ayah)<br> Ratumas Esa (ibu)\n| relatives          = [[Sultan Thaha Syaifuddin]] (kakek)\n}}"]


In [59]:
for key,value in properties.items():
    print(key,":",value)
    print("===========")

name :  Sultan Thaha Syaifuddin

title :  

titletext :  

image :  Sultan Thaha Syaifuddin.jpg

caption :  

succession :  [[Kesultanan Jambi#Daftar Penguasa|Sultan Jambi]] ke-20

reign :  1855 - 26 April 1904

date1 :  

date2 :  

reign-type :  

coronation :  

predecessor :  Sultan Abdurrahman Nazaruddin

successor :  

royal house :  

father :  Sultan Muhammad Fachruddin

issue :  

birth_date :  {{birth year|1816}}

birth_place :  [[Kota Jambi|Tanah Pilih]], [[Kesultanan Jambi]]

death_date :  {{death date|1904|4|26}} (87 atau 88 tahun)

death_place :  Betung Bedarah, [[Tebo Ilir, Tebo|Tebo Ilir]], [[Tebo]]



In [103]:
wikicode = mwparserfromhell.parse(properties['commander1'])
print(str(properties['commander1']))
temp = re.sub("<br>","{{br}}",str(properties['commander1']))
print(re.sub("{{br}}","\n",temp))

 {{flagicon|Belanda}} [[Johan Harmen Rudolf Köhler|Johan Köhler]]{{KIA}}
<br>{{flagicon|Belanda}} [[Jan van Swieten]] 
<br>{{flagicon|Belanda}} [[Johannes Ludovicius Jakobus Hubertus Pel|Johannes Pel]]{{KIA}}
<br>{{flagicon|Belanda}} [[Karel van der Heijden]]{{WIA}}
<br>{{flagicon|Belanda}} [[Henry Demmeni]]{{DOW}}
<br>{{flagicon|Belanda}} [[Jan Jacob Karel de Moulin]]{{KIA}}
<br>{{flagicon|Belanda}} [[G.C.E. van Daalen (1863-1930)|Gotfried van Daalen]]
<br>{{flagicon|Belanda}} [[Johan Cornelis van der Wijck]]
{{flagicon|Belanda}} [[Johannes Benedictus van Heutsz]]

 {{flagicon|Belanda}} [[Johan Harmen Rudolf Köhler|Johan Köhler]]{{KIA}}

{{flagicon|Belanda}} [[Jan van Swieten]] 

{{flagicon|Belanda}} [[Johannes Ludovicius Jakobus Hubertus Pel|Johannes Pel]]{{KIA}}

{{flagicon|Belanda}} [[Karel van der Heijden]]{{WIA}}

{{flagicon|Belanda}} [[Henry Demmeni]]{{DOW}}

{{flagicon|Belanda}} [[Jan Jacob Karel de Moulin]]{{KIA}}

{{flagicon|Belanda}} [[G.C.E. van Daalen (1863-1930)|Gotfried 

# military conflict

In [2]:
class Infobox():
    def __init__(self,title):
        self.title = title
        site = pywikibot.Site("id", "wikipedia")
        art = pywikibot.Page(site, self.title)
    

        wikicode = mwparserfromhell.parse(art.get())
        matches = wikicode.filter_templates(matches = self.type)
        self.infobox = {param.name.strip(): re.sub("\[\[File:[^\]]*\]\]","",re.sub("\[\[Berkas:[^\]]*\]\]","",str(param.value)))
                            for param in matches[0].params}
#         print(self.infobox)
        self.clean_infobox = self.clean_data()
        self.clean_infobox['wikititle'] = title
    def clean_coma(self,key):
        temp = self.infobox.get(key,"")
        temp = temp.split(",")
        res = []
        for i in temp:
            if i != "" :
                res.append(self.text(i.strip()))
        return res
    def clean_link(self,key):
        return self.filter_wikilinks(self.infobox.get(key,""))
    def clean_text(self,key):
        return self.text(self.infobox.get(key,""))
    def clean_list(self,key):
        return self.list(self.infobox.get(key,""))
    def clean_list2(self,key):
        return self.list2(self.infobox.get(key,""))
    def clean_br(self,key):
        temp = self.infobox.get(key,"")
        temp = re.sub("{{br}}","<br>",str(self.infobox.get(key,"")))
        temp = re.sub("<br />","<br>",temp)
        temp = re.sub("<br/>","<br>",temp)
        temp = re.sub("<br>","\n",temp)
        temp = temp.split("\n")
        res = []
        for i in temp:
            if i != "" :
                res.append(self.text(i.strip()))
        return res
    def clean_date_template(self,key):
        wikitext = self.infobox.get(key,"")
        temp = self.clean_birth_date(wikitext)
        if(temp != ""):
            return temp
        temp = self.clean_death_date_and_age(wikitext)
        if(temp != ""):
            return temp
        return self.clean_template(wikitext)
    def clean_date(self,key):
        data = self.infobox.get(key,"")
        temp = re.split("[-|\u2013]",data)
        print(temp)
        res={}
        if len(temp) > 0:
            res['start'] = self.text(temp[0].strip())
        if len(temp) > 1:
            res['end'] = self.text(temp[1].strip())
        return res
    def clean_template(self,key):
        wikitext = self.infobox.get(key,"")
        wikicode = mwparserfromhell.parse(wikitext)
        return re.sub("\n","",wikicode.strip_code(keep_template_params=True).strip())
    def template(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        return re.sub("\n","",wikicode.strip_code(keep_template_params=True).strip())
    def strip_template(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        return re.sub("\n","",wikicode.strip_code(keep_template_params=True).strip())
    def filter_wikilinks(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        link = wikicode.filter_wikilinks()
        temp = []
        for i in link:
            temp.append(str(i.title))
        return temp
    def text(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        return re.sub("\n","",wikicode.strip_code().strip())
    def list(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        template = wikicode.filter_templates(matches="ubl")
        temp = []
        if(len(template) > 0):
            for i in template[0].params :
                temp.append(str(self.text(i.value)))
        template = wikicode.filter_templates(matches="bulleted list")
        if(len(template) > 0):
            for i in template[0].params :
                temp.append(str(self.text(i.value)))
#         template = wikicode.filter_templates(matches="plainlist")
#         print(template)
#         if(len(template) > 0):
#             for i in str(template[0].params[0].value).split("*") :
#                 temp.append(str(self.text(i)))
        return temp
    def clean_marriage(self,key):
        wikitext = self.infobox.get(key,"")
        wikicode = mwparserfromhell.parse(wikitext)
        template = wikicode.filter_templates(matches="marriage")
        temp = []
        print(template)
        if(len(template) > 0):
            for i in template :
                temp.append(str(self.strip_template(i.params[0].value)))
        return temp
    def clean_birth_date(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        template = wikicode.filter_templates(matches="birth date")
        if(len(template) >0):
            date = ['January','February','March','April','May','June','July','August','September','October','November','December']
            temp = re.findall("\d+",self.template(wikitext))
            print(wikitext)
            print(temp)
            temp[1] = date[int(temp[1])-1]
            return "-".join(temp[::-1])
        return ""
    def clean_death_date_and_age(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        template = wikicode.filter_templates(matches="death date and age")
        if(len(template) >0):
            date = ['January','February','March','April','May','June','July','August','September','October','November','December']
            temp = re.findall("\d+",self.template(wikitext))
            print(wikitext)
            print(temp)
            temp[1] = date[int(temp[1])-1]
            return "-".join(temp[:3][::-1])
        return ""
    def list2(self,wikitext):
        wikicode = mwparserfromhell.parse(wikitext)
        template = wikicode.filter_templates(matches="ubl")
        temp = []
        if(len(template) > 0):
            for i in template[0].params :
                temp.append(str(self.strip_template(i.value)))
        template = wikicode.filter_templates(matches="bulleted list")
        if(len(template) > 0):
            for i in template[0].params :
                temp.append(str(self.strip_template(i.value)))
        template = wikicode.filter_templates(matches="plainlist")
        if(len(template) > 0):
            if(template[0].params[0].value!= "nowrap"):
                for i in str(template[0].params[0].value).split("*") :
                    temp.append(str(self.strip_template(i)))
            else :
                for i in str(template[0].params[1].value).split("*") :
                    temp.append(str(self.strip_template(i)))
        return temp
    

In [3]:
class Infobox_military_conflict(Infobox):
    def __init__(self,title):
        self.type = "Infobox Military Conflict"
        Infobox.__init__(self,title)
    def clean_data(self):
        temp = {}
        temp['conflict'] = self.clean_text('conflict')
        temp['partof'] = self.clean_text('partof')
        temp['image'] = self.clean_text('image')
        temp['caption'] = self.clean_text('caption')
        temp['date'] = self.clean_date('date')
        temp['place'] = self.clean_link('place')
        temp['casus'] = self.clean_text('casus')
        temp['teritory'] = self.clean_text('teritory')
        temp['result'] = self.clean_br('result')
        temp['combatant1'] = self.clean_list("combatant1")
        if(len(temp['combatant1']) == 0):
            temp['combatant1'] = self.clean_br('combatant1')
        temp['combatant2'] = self.clean_list("combatant2")
        if(len(temp['combatant2']) == 0):
            temp['combatant2'] = self.clean_br('combatant2')
        temp['commander1'] = self.clean_list("commander1")
        if(len(temp['commander1']) == 0):
            temp['commander1'] = self.clean_br('commander1')
        temp['commander2'] = self.clean_list("commander2")
        if(len(temp['commander2']) == 0):
            temp['commander2'] = self.clean_br('commander2')
        temp['units1'] = self.clean_list("units1")
        if(len(temp['units1']) == 0):
            temp['units1'] = self.clean_br('units1')
        temp['units2'] = self.clean_list("units2")
        if(len(temp['units2']) == 0):
            temp['units2'] = self.clean_br('units2')
        temp['strength1'] = self.clean_text('strength1')
        temp['strength2'] = self.clean_text('strength1')
        temp['casualties1'] = self.clean_text('casualties1')
        temp['casualties2'] = self.clean_text('casualties2')
        temp['notes'] = self.clean_text('notes')
        return temp
    

In [4]:
diponegoro = Infobox_military_conflict("Perang Diponegoro")
print(diponegoro.clean_infobox)

['21 Juli [[1825]] ', ' 9 Februari [[1830 1840]]\n']
{'conflict': 'Perang Diponegoro', 'partof': '', 'image': '', 'caption': 'Lukisan Peristiwa Penangkapan Pangeran Diponegoro oleh Raden Saleh', 'date': {'start': '21 Juli 1825', 'end': '9 Februari 1830 1840'}, 'place': ['Yogyakarta', 'Surakarta', 'Jawa Tengah', 'Jawa Timur'], 'casus': 'Jalan yang dibangun Belanda melintasi makam leluhur Pangeran Diponegoro 6', 'teritory': '', 'result': ['Kemenangan Belanda', 'Penangkapan dan pengasingan Pangeran Diponegoro ke MakassarToby Alice Volkman: Sulawesi: island crossroads of Indonesia, Passport Books, 1990, ISBN 0844299065,  page 73.'], 'combatant1': ['Belanda', 'Kesultanan Yogyakarta', 'Pasukan Tulungan'], 'combatant2': ['Pasukan Jawa/Diponegoro'], 'commander1': ['Hendrik M. de Kock', 'Hermanus W. Dotulong'], 'commander2': ['Diponegoro', 'Sentot Prawirodirdjo', 'Kiai Madja', 'Nyi Ageng Serang', 'Pakubuwana VI', 'Tumenggung Prawirodigdoyo'], 'units1': [], 'units2': [], 'strength1': '50.000', '

In [19]:
infobox = json.load(open("infobox\\json\\v1Infobox_Military_Conflict1.json"))
print(len(infobox))
daftar_infobox = []
for i in infobox :
    daftar_infobox.append(Infobox_military_conflict(i['entity']))
print(len(daftar_infobox))

11
['21 Juli [[1825]] ', ' 9 Februari [[1830 1840]]\n']
[' 1803', '1837\n']
[' 1873', '1904\n']
[' 15', '16 Juni 1908\n']
['22 Januari 1293', 'awal Agustus 1293{{sfn', 'Hung', '2022', 'p=7}} (8 bulan)\n']
[' 15', '19 Oktober 1945\n']
['  5 Agustus 1771 ', ' 11 Oktober 1772\n']
[' 19', '20 Juni 1812\n']
[' 20 November', '17 Desember [[1810]]\n']
['1641\n']
[' 1873', '1904\n']
11


In [29]:
key = 'date'
for i in daftar_infobox :
    print(i.infobox.get(key,""))
    print("-----------------")
    print(i.clean_infobox[key])
#     for j,k in i.clean_infobox.items():
#         print(j,":",k)
    print("################")

21 Juli [[1825]] - 9 Februari [[1830 1840]]

-----------------
{'start': '21 Juli 1825', 'end': '9 Februari 1830 1840'}
################
 1803–1837

-----------------
{'start': '1803', 'end': '1837'}
################
 1873–1904

-----------------
{'start': '1873', 'end': '1904'}
################
 15-16 Juni 1908

-----------------
{'start': '15', 'end': '16 Juni 1908'}
################
22 Januari 1293–awal Agustus 1293{{sfn|Hung|2022|p=7}} (8 bulan)

-----------------
{'start': '22 Januari 1293', 'end': 'awal Agustus 1293{{sfn'}
################
 15–19 Oktober 1945

-----------------
{'start': '15', 'end': '19 Oktober 1945'}
################
  5 Agustus 1771 - 11 Oktober 1772

-----------------
{'start': '5 Agustus 1771', 'end': '11 Oktober 1772'}
################
 19-20 Juni 1812

-----------------
{'start': '19', 'end': '20 Juni 1812'}
################
 20 November-17 Desember [[1810]]

-----------------
{'start': '20 November', 'end': '17 Desember 1810'}
################
1641

-----

In [25]:
a = "15-16 Juni 1908"
print(a.split("-"))

['15', '16 Juni 1908']


In [5]:
for i in daftar_infobox :
#     print(i.infobox['place'])
#     print("-----------------")
    for j,k in i.clean_infobox.items():
        print(j,":",k)
    print("################")

conflict : Perang Diponegoro
partof : 
image : 
caption : Lukisan Peristiwa Penangkapan Pangeran Diponegoro oleh Raden Saleh
date : 21 Juli 1825 - 9 Februari 1830 1840
place : ['Yogyakarta', 'Surakarta', 'Jawa Tengah', 'Jawa Timur']
casus : Jalan yang dibangun Belanda melintasi makam leluhur Pangeran Diponegoro 6
teritory : 
result : Kemenangan BelandaPenangkapan dan pengasingan Pangeran Diponegoro ke MakassarToby Alice Volkman: Sulawesi: island crossroads of Indonesia, Passport Books, 1990, ISBN 0844299065,  page 73.
combatant1 : ['Belanda', 'Kesultanan Yogyakarta', 'Pasukan Tulungan']
combatant2 : ['Pasukan Jawa/Diponegoro']
commander1 : ['Hendrik M. de Kock', 'Hermanus W. Dotulong']
commander2 : ['Diponegoro', 'Sentot Prawirodirdjo', 'Kiai Madja', 'Nyi Ageng Serang', 'Pakubuwana VI', 'Tumenggung Prawirodigdoyo']
units1 : []
units2 : []
strength1 : 50.000
strength2 : 50.000
casualties1 : 15.000
casualties2 : Serdadu Jawa:20,000 tewas dalam perangClodfelter, Michael, Warfare and Armed

In [148]:
string = "{{flagicon|Belanda}} [[Johannes Ludovicius Jakobus Hubertus Pel|Johannes Pel]]{{KIA}}"
print(re.sub("\{\{[^\}]*\}\}","",string))

['{{flagicon|Belanda}}', '{{KIA}}']


In [7]:
print(type([1,2,3]))

<class 'list'>


In [3]:
def to_csv(data,path,root):
    exist = []
    simple = []
    for info in data:
        for key,value in info.clean_infobox.items():
#             print(type(value))
            if(type(value) is list ):
                with open("infobox\\"+path+key+".csv",'a',encoding='utf-8') as file:
                    writer = csv.writer(file)
                    if not (key in exist):
                        writer.writerow(['key',key])
                        exist.append(key)
                    for i in value:
                        writer.writerow([info.clean_infobox[root],i])
            elif(type(value) is dict):
                with open("infobox\\"+path+key+"-date.csv",'a',encoding='utf-8') as file:
                    writer = csv.writer(file)
                    if not (key in exist):
                        writer.writerow(['key',"start-"+key,"end-"+key])
                        exist.append(key)
                    writer.writerow([info.clean_infobox[root],value['start'],value.get('end',"")])
            else:
                if not(key in simple):
                    simple.append(key)
    with open("infobox\\"+path+"simple.csv",'w',encoding="utf-8") as file:
        writer = csv.writer(file)
        writer.writerow(simple)
        print(simple)
        for info in data:
            temp = []
            for i in simple:
                temp.append(info.clean_infobox[i])
            writer.writerow(temp)
            
                

                


In [28]:
to_csv(daftar_infobox,"military_conflict\\",'wikititle')

['conflict', 'partof', 'image', 'caption', 'casus', 'teritory', 'strength1', 'strength2', 'casualties1', 'casualties2', 'notes', 'wikititle']


In [182]:
with open("infobox\\clean.json",'w') as file :
    out = []
    for i in daftar_infobox :
        out.append(i.clean_infobox)
    file.write(json.dumps(out))

# Infobox person

In [88]:
class Infobox_person(Infobox):
    def __init__(self,title):
        self.type = "Infobox person"
        Infobox.__init__(self,title)
    def clean_data(self):
        temp = {}
        temp['name'] = self.clean_text('name')
        temp['image'] = self.clean_text('image')
        temp['birth_place'] = self.clean_link('birth_place')
        temp['death_place'] = self.clean_link('death_place')
        temp['death_cause'] = self.clean_text('death_cause')
#         temp['resting_place_coordinates'] = self.clean_text('resting_place_coordinates')
        temp['monuments'] = self.clean_text('monuments')
        temp['ethnicity'] = self.clean_text('ethnicity')
        temp['occupation'] = self.clean_text('occupation')
        temp['religion'] = self.clean_text("religion")
        temp['denomination'] = self.clean_text("denomination")
        temp['parents'] = self.clean_br("parents")
        temp['awards'] = self.clean_text("awards")
        temp['caption'] = self.clean_text("caption")
        temp['nationality'] = self.clean_text("nationality")
        temp['spouse'] = self.clean_text('spouse')
        temp['birth_date'] = self.clean_text('birth_date')
        if temp['birth_date'] == "":
            temp['birth_date'] = self.clean_template('birth_date')
        temp['death_date'] = self.clean_text('death_date')
        if temp['death_date'] == "":
            temp['death_date'] = self.clean_template('death_date')
        temp['other_names'] = self.clean_text('other_names')
        temp['known_for'] = self.clean_text('known_for')
        temp['burial_place'] = self.clean_text('burial_place')
        temp['pre-nominals'] = self.clean_text('pre-nominals')
        temp['birth_name'] = self.clean_text('birth_name')
        temp['birthname'] = self.clean_text('birthname')
        temp['restingplace'] = self.clean_link('restingplace')
        temp['yearsactive'] = self.clean_text('yearsactive')
        temp['years_active'] = self.clean_text('years_active')
        temp['resting_place'] = self.clean_text('resting_place')
        
        temp['spouse-type'] = self.clean_text('spouse-type')
#         temp['module'] = self.clean_text('module')
        temp['title'] = self.clean_text('title')
        temp['father'] = self.clean_text('father')
        temp['house'] = self.clean_text('house')
        temp['partner'] = self.clean_text('partner')
        temp['mother'] = self.clean_text('mother')
        temp['website'] = self.clean_text('website')
        temp['relatives'] = self.clean_text('relatives')
        return temp

In [89]:
infobox = json.load(open("infobox\\json\\v1Infobox_person24.json"))
print(len(infobox))
daftar_infobox = []
for i in infobox :
    daftar_infobox.append(Infobox_person(i['entity']))
print(len(daftar_infobox))

11
11


In [82]:
property = set()
for i in daftar_infobox:
    for key,value in i.infobox.items():
        if re.sub("\s","",str(value)) != "" :
            property.add(key)
print(len(property))

for i in property :
    print(i)

41
birth_name
spouse-type
ethnicity
religion
image
alt
image_size
module
burial_place
birth_date
birth_place
pre-nominals
nationality
death_place
birthname
title
imagesize
other_names
father
death_cause
occupation
years_active
caption
restingplace
house
partner
awards
parents
name
spouse
denomination
known_for
monuments
mother
yearsactive
website
relatives
death_date
resting_place_coordinates
signature_type
resting_place


In [101]:
for i in daftar_infobox :
    print(i.infobox.get('signature_type',""))
    print("-----------------")
    print(i.clean_infobox['signature_type'])
#     for j,k in i.clean_infobox.items():
#         print(j,":",k)
    print("################")


-----------------

################

-----------------

################

-----------------

################

-----------------

################

-----------------

################
 Tanda tangan

-----------------
Tanda tangan
################

-----------------

################

-----------------

################

-----------------

################

-----------------

################

-----------------

################


# infobox office holder

In [4]:
def get_property(source,type):
    infobox = json.load(open(source))
    res = set()
    for i in infobox :
        title = i['entity']
        site = pywikibot.Site("id", "wikipedia")
        art = pywikibot.Page(site, title)
    

        wikicode = mwparserfromhell.parse(art.get())
        matches = wikicode.filter_templates(matches = type)
        if(len(matches) > 0):
            property = {param.name.strip(): re.sub("\[\[File:[^\]]*\]\]","",re.sub("\[\[Berkas:[^\]]*\]\]","",str(param.value)))
                                for param in matches[0].params}
            for key,value in property.items():
                if re.sub("\s","",str(value)) != "" :
                    res.add(key)

    print(len(res))

    for i in res :
        print(i)
    return res

In [5]:
get_property("infobox\\json\\v1Infobox_person24.json","Infobox person")

41
image_size
website
birth_name
death_place
caption
birthname
parents
restingplace
burial_place
image
partner
spouse-type
spouse
resting_place
known_for
father
signature_type
module
title
denomination
awards
ethnicity
resting_place_coordinates
monuments
other_names
mother
occupation
death_cause
birth_place
birth_date
death_date
nationality
religion
relatives
name
pre-nominals
imagesize
yearsactive
alt
years_active
house


{'alt',
 'awards',
 'birth_date',
 'birth_name',
 'birth_place',
 'birthname',
 'burial_place',
 'caption',
 'death_cause',
 'death_date',
 'death_place',
 'denomination',
 'ethnicity',
 'father',
 'house',
 'image',
 'image_size',
 'imagesize',
 'known_for',
 'module',
 'monuments',
 'mother',
 'name',
 'nationality',
 'occupation',
 'other_names',
 'parents',
 'partner',
 'pre-nominals',
 'relatives',
 'religion',
 'resting_place',
 'resting_place_coordinates',
 'restingplace',
 'signature_type',
 'spouse',
 'spouse-type',
 'title',
 'website',
 'years_active',
 'yearsactive'}

In [31]:
class Infobox_Officeholder(Infobox):
    def __init__(self,title,property):
        self.type = "Infobox Officeholder"
        self.property = property
        Infobox.__init__(self,title)
    def clean_data(self):
        temp = {}
        for i in self.property :
            temp[i] = self.clean_text(i)
        temp['branch'] = self.clean_list("branch")
        temp['monarch3'] = self.clean_br("monarch3")
        temp['president3'] = self.clean_br("president3")
        temp['allegiance'] = self.clean_list2('allegiance')
        if len(temp['allegiance']) == 0 :
            temp['allegiance'] = self.clean_text('allegiance')
        temp['predecessor'] = self.clean_br('predecessor')
        temp['monarch'] = self.clean_br("monarch")
        temp['death_date'] = self.clean_date_template('death_date')
        temp['parents'] = self.clean_br('parents')
        temp['president2'] = self.clean_br("president2")
        temp['birth_date'] = self.clean_date_template('birth_date')
        temp['monarch2'] = self.clean_br("monarch2")
        temp['spouse'] = self.clean_br('spouse')
        temp['children'] = self.clean_br('children')
        temp['successor'] = self.clean_br('successor')
        temp['president'] = self.clean_br("president")
        if temp['battles'] == "" :
            temp['battles'] = self.clean_list('battles')
        #death_place,birth_place
        return temp

In [32]:
source = "infobox\\json\\v1Infobox_Officeholder37.json"
info_type = "Infobox Officeholder"
daftar_property = get_property(source,info_type)


85
death_place
predecessor5
president3
president2
governor
branch
term_end1
predecessor2
succeeding
primeminister4
partner
primeminister
monarch
term_end3
allegiance
order4
monarch3
office2
unit
signature
successor2
president
death_date
order5
office
successor3
name
term_start
successor1
rank
primeminister3
predecessor4
president1
death_cause
term_start3
caption
term_end5
Term_start5
successor
term_end4
birth_date
office5
term_end2
co-leader
term_start5
order3
term_start1
birthname
honorific-prefix
term_start4
order2
parents
predecessor
office4
spouse
president4
primeminister1
image
relations
term_start2
birth_place
nationality
alma_mater
imagesize
title
footnotes
term_end
children
serviceyears
successor5
predecessor1
governor3
primeminister2
awards
order
predecessor3
profession
successor4
battles
office3
monarch2
otherparty
1
office1
religion


In [33]:
infobox = json.load(open(source))
print(len(infobox))
daftar_infobox = []
for i in infobox :
    daftar_infobox.append(Infobox_Officeholder(i['entity'],daftar_property))
print(len(daftar_infobox))

17
 {{death date and age|1899|2|11|1854}}

['1899', '2', '11', '1854']
 {{death date and age|1998|9|11|1910|4|10}}

['1998', '9', '11', '1910', '4', '10']
 {{birth date|1910|4|10}}

['1910', '4', '10']
 {{death date and age|1978|3|4|1897|4|20}}

['1978', '3', '4', '1897', '4', '20']
 {{birth date|1897|4|20}}

['1897', '4', '20']
 {{death date and age|df=yes|1818|5|2|1762|10|21}}

['1818', '5', '2', '1762', '10', '21']
 {{birth date|df=yes|1762|10|21}}

['1762', '10', '21']
 {{Death date and age|1978|08|16|1888|03|07}} 

['1978', '08', '16', '1888', '03', '07']
 {{Birth date|1888|03|07}}

['1888', '03', '07']
 {{death date and age|1899|2|11|1854}}

['1899', '2', '11', '1854']
 {{Death date and age|1750|11|01|1705|08|08}}

['1750', '11', '01', '1705', '08', '08']
 {{Death date and age|1845|04|12|1779|5|24}}

['1845', '04', '12', '1779', '5', '24']
 {{birth date|1779|5|25}}

['1779', '5', '25']
 {{death date and age|df=y|1838|5|23|1762|10|12}}

['1838', '5', '23', '1762', '10', '12']
 {{b

In [8]:
key = 'birth_date'
for i in daftar_infobox :
    print(i.infobox.get(key,""))
    print("-----------------")
    print(i.clean_infobox[key])
#     for j,k in i.clean_infobox.items():
#         print(j,":",k)
    print("################")

 

-----------------

################
 [[1772]]

-----------------

################
 [[1854]]

-----------------

################
 {{birth date|1910|4|10}}

-----------------
10-April-1910
################
 {{birth date|1897|4|20}}

-----------------
20-April-1897
################
 {{birth date|df=yes|1762|10|21}}

-----------------
21-October-1762
################
 [[1860]] (perkiraan)

-----------------

################
 {{Birth date|1888|03|07}}

-----------------
07-March-1888
################
 [[1772]]

-----------------

################
 [[1854]]

-----------------

################
 [[8 Agustus]] [[1705]]

-----------------

################
 {{birth date|1779|5|25}}

-----------------
25-May-1779
################
 {{birth date|df=y|1762|10|12}}

-----------------
12-October-1762
################
 1760

-----------------

################
 {{birth date|1938|5|7}}

-----------------
7-May-1938
################
 {{Birth date|1917|7|1}}

-----------------
1-July-1917
#########

In [9]:
print(daftar_infobox[0].clean_infobox)

{'order': '', 'successor3': '', 'death_cause': '', 'primeminister': '', 'president4': '', 'president3': [], 'term_start1': '', 'successor5': '', 'office': '', 'governor3': '', 'caption': 'Raja Haji Fisabilillah', 'order3': '', 'term_start4': '', 'office2': '', 'religion': 'Islam', 'branch': [], 'monarch2': [], 'term_end4': '', 'office1': '', 'nationality': 'Indonesia', 'term_start2': '', 'Term_start5': '', 'death_place': '', 'monarch': [], 'unit': '', 'governor': '', 'parents': [''], 'honorific-prefix': '', 'imagesize': '200px', 'order4': '', 'order5': '', 'rank': '', 'battles': [], 'office5': '', 'predecessor5': '', 'term_end3': '', 'alma_mater': '', 'president': [], 'otherparty': '', 'term_start': '', 'term_end': '', 'successor': [''], 'successor2': '', 'primeminister1': '', 'awards': '', 'term_end1': '', 'monarch3': [], 'children': [], 'order2': '', 'birthname': '', 'successor4': '', 'relations': '', 'president1': '', 'co-leader': '', 'office4': '', 'birth_date': '', 'signature': ''

In [34]:
to_csv(daftar_infobox,"office_holder\\",'wikititle')

['death_place', 'predecessor5', 'governor', 'term_end1', 'predecessor2', 'succeeding', 'primeminister4', 'partner', 'primeminister', 'term_end3', 'allegiance', 'order4', 'office2', 'unit', 'signature', 'successor2', 'death_date', 'order5', 'office', 'successor3', 'name', 'term_start', 'successor1', 'rank', 'primeminister3', 'predecessor4', 'president1', 'death_cause', 'term_start3', 'caption', 'term_end5', 'Term_start5', 'term_end4', 'birth_date', 'office5', 'term_end2', 'co-leader', 'term_start5', 'order3', 'term_start1', 'birthname', 'honorific-prefix', 'term_start4', 'order2', 'office4', 'president4', 'primeminister1', 'image', 'relations', 'term_start2', 'birth_place', 'nationality', 'alma_mater', 'imagesize', 'title', 'footnotes', 'term_end', 'serviceyears', 'successor5', 'predecessor1', 'governor3', 'primeminister2', 'awards', 'order', 'predecessor3', 'profession', 'successor4', 'office3', 'otherparty', '1', 'office1', 'religion', 'wikititle', 'battles']


# infobox_military_person

In [5]:
class Infobox_Military_Person(Infobox):
    def __init__(self,title,property):
        self.type = "Infobox military person"
        self.property = property
        Infobox.__init__(self,title)
    def clean_data(self):
        temp = {}
        for i in self.property :
            temp[i] = self.clean_text(i)
        temp['awards'] = self.clean_list2('awards')
#         print(temp['awards'])
        if(len(temp['awards']) == 0):
            temp['awards'] = self.clean_br('awards')
#         print(temp['awards'])
        temp['spouse'] = self.clean_marriage('spouse')
        print(temp['spouse'])
        if(len(temp['spouse'])==0):
            temp['spouse'] = self.clean_br('spouse')
        print(temp['spouse'])
        temp['children'] = self.clean_br('children')
        temp['period'] = self.clean_date('period')
        temp['rank'] = self.clean_template('rank')
        temp['battles'] = self.clean_list2('battles')
        if(len(temp['battles']) == 0):
            temp['battles'] = self.clean_br('battles')
        temp['commands'] = self.clean_list2('commands')
        if(len(temp['commands']) == 0):
            temp['commands'] = self.clean_br('commands')
        temp['death_date'] = self.clean_date_template('death_date')
        temp['allegiance'] = self.clean_template("allegiance")
        temp['birth_date'] = self.clean_date_template('birth_date')
        temp['serviceyears'] = self.clean_date('serviceyears')
        return temp

In [6]:
source = "infobox\\json\\v1Infobox_military_person61.json"
info_type = "Infobox military person"
daftar_property = get_property(source,info_type)

32
branch
commands
placeofburial_coordinates
image_size
death_place
nickname
birth_name
birth_date
allegiance
image
spouse
death_date
branch_label
caption
rank
native_name_lang
website
religion
children
servicenumber
name
birth_place
native_name
unit
battles
serviceyears
battles_label
laterwork
period
width_style
serviceyears_label
awards


In [7]:
infobox = json.load(open(source))
print(len(infobox))
daftar_infobox = []
for i in infobox :
    daftar_infobox.append(Infobox_Military_Person(i['entity'],daftar_property))
print(len(daftar_infobox))

12
[]
[]
['I Gusti Ayu Made Geria', 'I Gusti Ayu Kompyang', 'Gusti Biyang Made Saji', 'Jero Sekar']
['']
['']
[]
[]
[]
['']
 {{Death date and age|1817|12|16|1783|06|08|df=yes}}

['1817', '12', '16', '1783', '06', '08']
 {{Birth date|1783|06|08|df=yes}}

['1783', '06', '08']
['\n']
['{{marriage|Agneta C. Roqué|1912|1925}}', '{{marriage|Anna Maria Bergman|1934}}']
['Agneta C. Roqué', 'Anna Maria Bergman']
['Agneta C. Roqué', 'Anna Maria Bergman']
['']
 {{Death date and age|df=yes|1968|1|15|1887|11|21}}

['1968', '1', '15', '1887', '11', '21']
 {{Birth date|df=yes|1887|11|21}}

['1887', '11', '21']
[' 1908', '1945\n']
[]
[]
[]
['']
 {{birth date|1886|10|11|df=y}}

['1886', '10', '11']
[' 1907', '1949\n']
[]
[]
[]
['']
 {{death date and age|1946|06|12|1879|08|08}}

['1946', '06', '12', '1879', '08', '08']
{{birth date|1879|08|08}}

['1879', '08', '08']
[' 1900', '1945\n']
[]
[]
[]
['']
{{death date and age|df=y|1968|10|04|1886|06|28}}

['1968', '10', '04', '1886', '06', '28']
{{birth date|

In [145]:
key = 'serviceyears'
for i in daftar_infobox :
    print(i.infobox.get(key,""))
    print("-----------------")
    print(i.clean_infobox[key])
#     for j,k in i.clean_infobox.items():
#         print(j,":",k)
    print("################")


-----------------
{'start': ''}
################


-----------------
{'start': ''}
################
 1908–1945

-----------------
{'start': '1908', 'end': '1945'}
################
 1907–1949

-----------------
{'start': '1907', 'end': '1949'}
################
 1900–1945

-----------------
{'start': '1900', 'end': '1945'}
################
 1907 - 1945

-----------------
{'start': '1907', 'end': '1945'}
################
1911–1944

-----------------
{'start': '1911', 'end': '1944'}
################

-----------------
{'start': ''}
################
 1906–1942
 
-----------------
{'start': '1906', 'end': '1942'}
################
 1822-1874

-----------------
{'start': '1822', 'end': '1874'}
################
1909–1945

-----------------
{'start': '1909', 'end': '1945'}
################
 1914-1945

-----------------
{'start': '1914', 'end': '1945'}
################


In [16]:
to_csv(daftar_infobox,"military_person\\",'wikititle')

['width_style', 'native_name_lang', 'religion', 'death_place', 'laterwork', 'website', 'native_name', 'placeofburial_coordinates', 'birth_place', 'unit', 'servicenumber', 'name', 'branch', 'allegiance', 'birth_date', 'caption', 'image_size', 'death_date', 'image', 'rank', 'serviceyears_label', 'nickname', 'battles_label', 'branch_label', 'birth_name', 'wikititle']


In [8]:
def isolate(daftar_infobox,prop,path):
    with open(path,'w') as file:
        writer = csv.writer(file)
        writer.writerow(prop)
        
        for i in daftar_infobox:
            temp = []
            for j in prop:
                temp.append(i.clean_infobox[j])
            writer.writerow(temp)

In [10]:
isolate(daftar_infobox,['wikititle','birth_date','death_date'],"infobox\\military_person_date.csv")

# infobox royalty

In [11]:
class Infobox_Royalty(Infobox):
    def __init__(self,title,property):
        self.type = "Infobox royalty"
        self.property = property
        Infobox.__init__(self,title)
    def clean_data(self):
        temp = {}
        for i in self.property :
            temp[i] = self.clean_text(i)
        temp['spouse'] = self.clean_coma("spouse")
        if(len(temp['spouse']) <2):
            temp['spouse'] = self.clean_br('spouse')
        temp['alongside5'] = self.clean_coma('alongside5')
        temp['alongside6'] = self.clean_coma('alongside6')
        temp['title'] = self.clean_br('title')
        temp['children'] = self.clean_br('children')
        temp['death_date'] = self.clean_date_template('death_date')
        if(temp['death_date'] == ""):
            temp['death_date'] = self.clean_text('death_date')
        temp['birth_date'] = self.clean_date_template('birth_date')
        if(temp['birth_date'] == ""):
            temp['birth_date'] = self.clean_text('birth_date')
        temp['battles'] = self.clean_list2('battles')
        return temp

In [12]:
source = "infobox\\json\\v1Infobox_royalty42.json"
info_type = "Infobox royalty"
daftar_property = get_property(source,info_type)

163
pre-type
branch
predecessor4
president11
image_size
house
consort
burial_place
reg-type
term_start6
term_start10
order14
spouses
term_start8
1namedata
1blankname1
image
predecessor
cor-type
module
office2
successor10
regent
office10
lieutenant2
term_end8
issue-type
signature_type
successor13
rank
father
term_end15
children
moretext
president4
reg-type2
successor4
given_name
house-type
office3
predecessor5
term_start9
alongside5
serviceyears
native-name
issue-link
term_start12
term_start14
succession2
native_lang1_name1
term_start4
term_start5
president15
death_place
predecessor3
office14
succession1
predecessor9
queen
order9
predecessor14
successor14
native_lang1
spouse-type
term_end14
term_end9
term_start
president3
posthumous name
reign-type
term_start3
term_end3
term_start13
predecessor2
predecessor13
1
successor3
term_start15
royal house
office
successor15
mother
coronation1
successor11
1namedata1
order4
honorific-prefix
reign-type2
term_label
signature
term_label5
office8
issu

In [13]:
infobox = json.load(open(source))
print(len(infobox))
daftar_infobox = []
for i in infobox :
    daftar_infobox.append(Infobox_Royalty(i['entity'],daftar_property))
print(len(daftar_infobox))

50
 {{death date and age|1670|6|12|1631|1|12|df=y}}

['1670', '6', '12', '1631', '1', '12']
 {{Death date and age|1849|6|2|1807|5|26}}

['1849', '6', '2', '1807', '5', '26']
 {{birth date|1528|2|10|df=yes}} (?)

['1528', '2', '10']
 {{death date and age|1939|2|22|1866|11|29}}

['1939', '2', '22', '1866', '11', '29']
 {{birth date|1866|11|29}}

['1866', '11', '29']
 {{death date and age|1792|3|24|1717|8|5|df=y}}

['1792', '3', '24', '1717', '8', '5']
 {{death date and age|1906|9|20|1876|4|5|df=y}}

['1906', '9', '20', '1876', '4', '5']
 {{death date and age|1855|1|8|1785|11|11|df=y}}

['1855', '1', '8', '1785', '11', '11']
 {{death date and age|1829|10|4|1764|3|31|df=y}}

['1829', '10', '4', '1764', '3', '31']
 {{death date and age|1828|1|3|1750|3|7|df=y}}

['1828', '1', '3', '1750', '3', '7']
 {{death date and age|1814|11|3|1769|2|20|df=y}}

['1814', '11', '3', '1769', '2', '20']
 {{Death date and age|1849|6|2|1807|5|26}}

['1849', '6', '2', '1807', '5', '26']
 {{death date and age|190

In [97]:
key = 'battles'
for i in daftar_infobox :
    print(i.infobox.get(key,""))
    print("-----------------")
    print(i.clean_infobox[key])
#     for j,k in i.clean_infobox.items():
#         print(j,":",k)
    print("################")


-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
################

-----------------
[]
###

In [98]:
to_csv(daftar_infobox,"royalty\\",'wikititle')

['moretext', 'predecessor13', '1', 'office14', 'consort', 'native_lang1_name1', 'term_end11', 'regnal name', 'term_start3', 'father', 'spouse-type', 'mother', 'order2', 'office15', 'term_end10', 'order14', 'rank', 'successor2', 'predecessor15', '1namedata1', 'successor10', '1blankname1', '1namedata', 'succession1', 'order8', 'module', 'date of burial', 'succession2', 'honorific_prefix', 'president3', 'predecessor14', 'president2', 'term_start12', 'spouses', 'predecessor11', 'reign-type', 'office10', 'term_end9', 'successor12', 'president11', '1blankname', 'reign', 'reign1', 'president4', 'successor13', 'signature', 'native_lang1', 'term_end8', 'house', 'native_name', 'term_start11', 'predecessor2', 'term_start4', 'term_label', 'birth_name', 'royal house', 'lieutenant8', 'birth_place', 'issue-type', 'lieutenant2', 'successor6', 'occupation', 'religion', 'posthumous name', 'office3', 'office2', 'term_start6', 'term_end12', 'suc-type', 'successor3', 'term_label5', 'cor-type', 'imgw', 'iss

In [14]:
isolate(daftar_infobox,['wikititle','birth_date','death_date'],"infobox\\royalty_date.csv")

In [3]:
import pandas as pd
from geopy.geocoders import Nominatim

geolocator = Nominatim(user_agent='indonesian-history-ontology')

def get_lat_lon(place, attempt=1, max_attempts=5):
    location = geolocator.geocode(place, geometry='wkt')
    if location:
        print(place)
        print("location: " + str(location))
        print(location.raw)
        print(location.raw['geotext'])
        print()
        return pd.Series((location.latitude, location.longitude, location.raw['geotext']))
    else:
        return pd.Series((-0.789275, 113.921327))

df = pd.read_csv('infobox\\military_conflict\\place.csv')

df[['latitude', 'longitude', 'location']] = df['place'].apply(get_lat_lon)

df.to_csv('infobox\\fix-military-conflict-cleaned-no-multivalued.csv', index=False)

Yogyakarta
location: Daerah Istimewa Yogyakarta, Jawa, Indonesia
{'place_id': 58130190, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 5616105, 'lat': '-7.9778383999999996', 'lon': '110.36722565020224', 'class': 'boundary', 'type': 'administrative', 'place_rank': 8, 'importance': 0.5435224580914347, 'addresstype': 'state', 'name': 'Daerah Istimewa Yogyakarta', 'display_name': 'Daerah Istimewa Yogyakarta, Jawa, Indonesia', 'boundingbox': ['-8.4159039', '-7.5412887', '109.9017890', '110.8386897'], 'geotext': 'POLYGON((109.901789 -8.1330094,110.1245895 -8.2070496,110.2662964 -8.2541339,110.3726995 -8.2894843,110.6383904 -8.387396,110.666379 -8.3954785,110.7822725 -8.4159039,110.8346271 -8.2033536,110.8337375 -8.2006013,110.8330721 -8.198596,110.8332753 -8.1966494,110.8332664 -8.1954686,110.8341121 -8.1940623,110.8347094 -8.1916679,110.8346862 -8.1900904,110.8347585 -8.1894921,110.8346868 -8.1887262,110.834471 -8.187816

Surakarta
location: Surakarta, Kecamatan Pasar Kliwon, Jawa Tengah, Jawa, Indonesia
{'place_id': 59040543, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 9687063, 'lat': '-7.5692489', 'lon': '110.828448', 'class': 'boundary', 'type': 'administrative', 'place_rank': 12, 'importance': 0.49990210704489074, 'addresstype': 'city', 'name': 'Surakarta', 'display_name': 'Surakarta, Kecamatan Pasar Kliwon, Jawa Tengah, Jawa, Indonesia', 'boundingbox': ['-7.5952116', '-7.5232191', '110.7690994', '110.8689442'], 'geotext': 'POLYGON((110.7690994 -7.5513984,110.7703329 -7.5518066,110.7703932 -7.5518269,110.7705773 -7.5518822,110.7709949 -7.5520042,110.7715629 -7.5521675,110.7719659 -7.5522921,110.771966 -7.5522921,110.7733651 -7.5527139,110.773527 -7.5527652,110.7736229 -7.5527843,110.7738216 -7.5528366,110.7742398 -7.5529829,110.7745642 -7.5530937,110.7746731 -7.5531282,110.7747149 -7.5531412,110.7750764 -7.5532338,110.7755156 

Jawa Tengah
location: Jawa Tengah, Jawa, Indonesia
{'place_id': 60855490, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 2388357, 'lat': '-7.3032412', 'lon': '110.0044145', 'class': 'boundary', 'type': 'administrative', 'place_rank': 8, 'importance': 0.6626261885869811, 'addresstype': 'state', 'name': 'Jawa Tengah', 'display_name': 'Jawa Tengah, Jawa, Indonesia', 'boundingbox': ['-8.4411879', '-4.0387936', '108.5558548', '111.8689695'], 'geotext': 'POLYGON((108.5558548 -7.2885941,108.5561371 -7.2891134,108.5567399 -7.2897643,108.5574418 -7.2906741,108.5586701 -7.2917599,108.5595551 -7.2923473,108.5600052 -7.2927812,108.5601349 -7.2932352,108.5600815 -7.2945942,108.5599061 -7.2961901,108.5598069 -7.2980889,108.5599976 -7.2992548,108.5603791 -7.300444,108.5612564 -7.3014411,108.5620118 -7.3020495,108.5641556 -7.3050607,108.5643511 -7.3057395,108.5645404 -7.3059393,108.5647049 -7.3061368,108.5651815 -7.3066613,108.5660

Jawa Timur
location: Jawa Timur, Jawa, Indonesia
{'place_id': 56220438, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 3438227, 'lat': '-7.6977397', 'lon': '112.4914199', 'class': 'boundary', 'type': 'administrative', 'place_rank': 8, 'importance': 0.6561969233127262, 'addresstype': 'state', 'name': 'Jawa Timur', 'display_name': 'Jawa Timur, Jawa, Indonesia', 'boundingbox': ['-9.0301357', '-4.8926893', '110.8815987', '116.4841801'], 'geotext': 'POLYGON((110.8815987 -8.4411879,111.4723645 -8.5666298,111.6728153 -8.6024668,111.6955918 -8.6052238,113.2644662 -8.7058038,114.492558 -8.9836109,114.7568198 -9.01156,114.9324661 -9.0301357,114.8854965 -8.9067149,114.7752986 -8.6401244,114.5538044 -8.5152306,114.4238367 -8.3178517,114.4126778 -8.1675452,114.4218326 -8.1057762,114.43095 -8.0839225,114.4506244 -8.0658685,114.4932807 -8.0329896,114.6404548 -7.7458479,114.9405777 -7.4627963,115.6975688 -7.5120245,116.3402876 -7.5

Sumatera Barat
location: Sumatera Barat, Sumatera, Indonesia
{'place_id': 60131642, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 2390841, 'lat': '-0.5827529', 'lon': '100.6133379', 'class': 'boundary', 'type': 'administrative', 'place_rank': 8, 'importance': 0.579602096724355, 'addresstype': 'state', 'name': 'Sumatera Barat', 'display_name': 'Sumatera Barat, Sumatera, Indonesia', 'boundingbox': ['-3.8839573', '0.9067222', '98.2364008', '101.8928830'], 'geotext': 'POLYGON((98.2364008 -1.0336376,98.4334704 -1.3320931,98.7059024 -1.781805,98.7214782 -1.8039793,98.7399373 -1.8238198,98.9354885 -2.0073893,99.8447377 -2.9644569,100.1763796 -3.4245819,100.6204863 -3.8839573,100.8822748 -3.4500358,100.9320805 -3.2635853,100.8036491 -2.8539738,100.7214698 -2.6898076,101.0218942 -2.4784515,101.0231562 -2.4780164,101.0353356 -2.4693147,101.0904783 -2.4305475,101.1018035 -2.4228095,101.115969 -2.4126258,101.1246473 -2.4067259

...

Kota Semarang
location: Semarang, Bengkulu, Muara Bangkahulu, Bengkulu, Sumatera, 38119, Indonesia
{'place_id': 59650282, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'node', 'osm_id': 3080068697, 'lat': '-3.7833248', 'lon': '102.2962039', 'class': 'place', 'type': 'village', 'place_rank': 19, 'importance': 0.27501, 'addresstype': 'village', 'name': 'Semarang', 'display_name': 'Semarang, Bengkulu, Muara Bangkahulu, Bengkulu, Sumatera, 38119, Indonesia', 'boundingbox': ['-3.8033248', '-3.7633248', '102.2762039', '102.3162039'], 'geotext': 'POINT(102.2962039 -3.7833248)'}
POINT(102.2962039 -3.7833248)

Jawa Tengah
location: Jawa Tengah, Jawa, Indonesia
{'place_id': 60855490, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 2388357, 'lat': '-7.3032412', 'lon': '110.0044145', 'class': 'boundary', 'type': 'administrative', 'place_rank': 8, 'importance': 0.6626261885869811,

Indonesia
location: Indonesia
{'place_id': 55825470, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 304751, 'lat': '-2.4833826', 'lon': '117.8902853', 'class': 'boundary', 'type': 'administrative', 'place_rank': 4, 'importance': 0.8155820405486824, 'addresstype': 'country', 'name': 'Indonesia', 'display_name': 'Indonesia', 'boundingbox': ['-11.2085669', '6.2744496', '94.7717124', '141.0194444'], 'geotext': 'POLYGON((94.7717124 5.7969898,94.7890119 5.7120818,95.017017 5.1985882,95.1626163 4.8361915,95.1844002 2.9801544,95.1896251 2.941682,95.2002809 2.9043431,95.2080587 2.8860085,95.2327169 2.8451547,95.2648325 2.8098449,95.7834513 2.3808549,96.7203878 1.4586943,96.8682399 1.3131333,96.8813572 1.192972,96.8906614 1.1510108,96.9083037 1.1118602,97.0679326 0.8411163,97.1868092 0.639479,97.6635815 -0.1692715,97.6766991 -0.1887911,97.6912489 -0.2079011,98.2364008 -1.0336376,98.4334704 -1.3320931,98.7059024 -1.781805,98.7

Songgon, Banyuwangi
location: Songgon, Banyuwangi, Jawa Timur, Jawa, 68463, Indonesia
{'place_id': 369419895, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'node', 'osm_id': 11238898625, 'lat': '-8.2331097', 'lon': '114.20228', 'class': 'place', 'type': 'town', 'place_rank': 18, 'importance': 0.30000999999999994, 'addresstype': 'town', 'name': 'Songgon', 'display_name': 'Songgon, Banyuwangi, Jawa Timur, Jawa, 68463, Indonesia', 'boundingbox': ['-8.2731097', '-8.1931097', '114.1622800', '114.2422800'], 'geotext': 'POINT(114.20228 -8.2331097)'}
POINT(114.20228 -8.2331097)

Kabupaten Banyuwangi
location: Area Kaliagung, Afdeling Pacaua, Kebun Sungailembu, Desa Sumberagung, Kecamatan Pesanggaran, Kabupaten Banyuwangi, Dusun Sungai Lembu, Banyuwangi, Jawa Timur, Jawa, Indonesia
{'place_id': 56657664, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'way', 'osm_id': 182556209, 'lat': '-8.53116335

Melaka
location: Melaka, Malaysia
{'place_id': 252567636, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 2939673, 'lat': '2.3293744', 'lon': '102.2880962', 'class': 'boundary', 'type': 'administrative', 'place_rank': 8, 'importance': 0.5578127202710209, 'addresstype': 'state', 'name': 'Melaka', 'display_name': 'Melaka, Malaysia', 'boundingbox': ['1.8395347', '2.4990483', '101.8327984', '102.5943828'], 'geotext': 'MULTIPOLYGON(((101.8327984 2.2132683,101.8438836 2.2049184,102.1158593 2.0011654,102.2233333 1.92,102.31018 1.8618555,102.3474851 1.8395347,102.4894508 2.0989705,102.4892964 2.1000248,102.4892084 2.1006099,102.4891444 2.1013545,102.4890497 2.1022364,102.489035 2.1023487,102.4888965 2.103097,102.4888654 2.1032335,102.4886857 2.1037976,102.4886168 2.1039543,102.4883278 2.1045439,102.488236 2.1047795,102.4881544 2.1050469,102.4881101 2.1055128,102.4882324 2.1057537,102.4883104 2.105865,102.4887733 2.1062888,10

Malaysia
location: Malaysia
{'place_id': 254816905, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 2108121, 'lat': '4.5693754', 'lon': '102.2656823', 'class': 'boundary', 'type': 'administrative', 'place_rank': 4, 'importance': 0.7674875088743168, 'addresstype': 'country', 'name': 'Malaysia', 'display_name': 'Malaysia', 'boundingbox': ['0.8538205', '8.3801468', '98.7365109', '119.4699634'], 'geotext': 'MULTIPOLYGON(((98.7365109 5.6847647,98.7365141 5.6841931,98.7365116 5.6836215,98.7365228 5.6826235,98.7365284 5.6816256,98.7365406 5.681054,98.736547 5.6804825,98.7365739 5.6794848,98.7365951 5.678487,98.7366162 5.6779158,98.7366316 5.6773444,98.7366742 5.6763473,98.736711 5.67535,98.7367411 5.6747791,98.7367655 5.674208,98.7368236 5.6732117,98.7368761 5.6722151,98.7369151 5.6716448,98.7369484 5.6710741,98.7370222 5.6700789,98.7370903 5.6690832,98.7371382 5.6685136,98.7371805 5.6679435,98.7372698 5.6669495,98.7373535 

In [7]:
import wikipedia

def retrieve_paragraph(article_title):
    wikipedia.set_lang("id")
    return wikipedia.summary(article_title,sentences=5,auto_suggest=False)

def get_url_wikipedia(article_title):
    wikipedia.set_lang("id")
    page = wikipedia.page(article_title,auto_suggest=False)
    return page.url

In [17]:
source = "infobox\\json\\v1Infobox_Officeholder37.json"
infobox = json.load(open(source))
daftar_infobox = []
for i in infobox :
    daftar_infobox.append({"title":i['entity'],
                            "url":get_url_wikipedia(i['entity']),
                             "summary":retrieve_paragraph(i['entity'])})
with open("infobox\\officeholder_summary.csv",'w',encoding="utf-8") as file:
        writer = csv.writer(file)
        writer.writerow(["title","url",'summary'])
        
        for i in daftar_infobox:
            writer.writerow(i.values())